In [1]:
import pandas as pd
import glob
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
import spacy
import pyLDAvis.gensim_models
pyLDAvis.enable_notebook()# Visualise inside a notebook
import en_core_web_md
from gensim.corpora.dictionary import Dictionary
from gensim.models import LdaMulticore
from gensim.models import CoherenceModel
import re

import pandas as pd
import gensim
import numpy as np
from gsdmm import MovieGroupProcess
from textblob import TextBlob
from gensim.parsing.preprocessing import remove_stopwords
from gensim.parsing.preprocessing import STOPWORDS
from gensim.corpora.textcorpus import lower_to_unicode
from nltk.corpus import stopwords
import nltk

import pandas as pd
import re
import nltk

nltk.download('stopwords')
from nltk.corpus import stopwords

nltk.download('punkt')
from nltk.tokenize import word_tokenize
from nltk.stem.porter import PorterStemmer
stemmer = PorterStemmer()
from string import punctuation

/opt/homebrew/lib/python3.9/site-packages/gensim/matutils.py:22: DeprecationWarning: Please use `triu` from the `scipy.linalg` namespace, the `scipy.linalg.special_matrices` namespace is deprecated.
  from scipy.linalg.special_matrices import triu
[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/swalke28/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /Users/swalke28/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [2]:
fulltext_id = []
fulltext = []
files = glob.glob("/Users/swalke28/Dropbox (ASU)/Allan-Shawn News Article Share/Text Data - all/*.txt")

In [3]:
# If you'd like to add additional stopwords
stop = STOPWORDS.union(set(['say', 'year', 'said', 'says', 'mr', 'year', 'years', 'people', 'like', 'time', 'www', 'center', 'san', 'diego', 'years', 'los', 'angeles', 'org', 'ave', 'sunday', 'saturday']))
# How many topics would you like
# Expirement with this number
num1 = 20

def process_text_list(fulltext):
    clean_text = []
    for text in fulltext:
        text = re.sub('[^A-Za-z]', ' ', text.lower())
        tokenized_text = word_tokenize(text)
        clean_text.append([
        word for word in tokenized_text if word not in stop and len(word) > 2
        ])


    return clean_text

def process_text(text):
    text = re.sub('[^A-Za-z]', ' ', text.lower())
    text = re.sub('united states', 'unitedstates', text.lower())
    tokenized_text = word_tokenize(text)
    return [
        word for word in tokenized_text if word not in stop and len(word) > 2
        ]

#tokens = process_text(fulltext)

In [4]:

for file in files:
    f = open(file, "r")
    id = re.findall(r"\/Users\/swalke28\/Dropbox \(ASU\)\/Allan-Shawn News Article Share/Text Data - all\/(.+)\.txt$", file)[0]
    text = f.read()
    entry = {'id': id, 'text': text, 'tokens': process_text(text), 'exclusion': 0, 'undocumented': 0, 'refugee': 0, 'asylum': 0, 'migrant': 0, 'dreamer': 0, 'unaccompanied': 0, 'citizenship': 0, 'immigration_reform': 0, 'border': 0, 'detention': 0, 'sanctuary': 0}

    fulltext_id.append(entry)
    fulltext.append(text)

In [5]:
df = pd.DataFrame.from_dict(fulltext_id)
exclusion_words = ['africa', 'arab', 'bosnian', 'delhi', 'eu', 'euro zone', 'europe', 'european', 'gaza', 'german', 'germany', 'gulf', 'hong kong', 'iran', 'iraq', 'iraqi', 'ireland', 'islamic state', 'israel', 'israeli', 'kim jong', 'korea', 'middle east', 'north korean', 'palestinian', 'persian gulf', 'russia', 'russian', 'saudi', 'south africa', 'soviet', 'sudan', 'tel aviv', 'united arab', 'united kingdom', 'west bank', 'yasser', 'nato']

for word in exclusion_words:
    df.loc[df['text'].str.contains(word, case=False), 'exclusion'] = 1

df.loc[df['text'].str.contains("citizenship", case=False), 'citizenship'] = 1
df.loc[df['text'].str.contains("immigration reform", case=False), 'immigration_reform'] = 1
df.loc[df['text'].str.contains("border", case=False), 'border'] = 1
df.loc[df['text'].str.contains("borders", case=False), 'border'] = 1
df.loc[df['text'].str.contains("detention", case=False), 'detention'] = 1
df.loc[df['text'].str.contains("deportation", case=False), 'deport'] = 1
df.loc[df['text'].str.contains("deport", case=False), 'deport'] = 1
df.loc[df['text'].str.contains("sanctuary", case=False), 'sanctuary'] = 1
df.loc[df['text'].str.contains("unaccompanied", case=False), 'unaccompanied'] = 1

for word in ['dreamer', 'dreamers', 'daca']:
    df.loc[df['text'].str.contains(word, case=False), 'dreamer'] = 1

for word in ['migrant', 'migrants']:
    df.loc[df['text'].str.contains(word, case=False), 'migrant'] = 1

for word in ['asylum seeker', 'asylum seekers']:
    df.loc[df['text'].str.contains(word, case=False), 'asylum'] = 1

for word in ['refugee', 'refugees']:
    df.loc[df['text'].str.contains(word, case=False), 'refugee'] = 1

for word in ['undocumented immigrant', 'undocumented immigrants']:
    df.loc[df['text'].str.contains(word, case=False), 'undocumented'] = 1

In [6]:
# Our spaCy model:
nlp = en_core_web_md.load()


In [7]:
def runLDA(tokens):

    # I will apply the Dictionary Object from Gensim, which maps each word to their unique ID:
    dictionary = Dictionary(tokens)
    corpus = [dictionary.doc2bow(doc) for doc in tokens]
    # Make a index to word dictionary.
    id2word = dictionary.id2token


    lda_model = LdaMulticore(corpus=corpus, id2word=dictionary, iterations=50, num_topics=100, workers = 8, passes=10,  alpha='asymmetric')
    # Compute Perplexity
    print('\nPerplexity: ', lda_model.log_perplexity(corpus))  
    # a measure of how good the model is. lower the better.

    # Compute Coherence Score
    #coherence_model_lda = CoherenceModel(model=lda_model, texts=corpus, dictionary=dictionary, coherence='c_v')
    #coherence_lda = coherence_model_lda.get_coherence()
    #print('\nCoherence Score: ', coherence_lda)

    return lda_model

# Crisis Only (without exclusion words in Excel)

In [36]:
tokens = df[df['exclusion'] == 0]['tokens'].tolist()
# I will apply the Dictionary Object from Gensim, which maps each word to their unique ID:
dictionary = Dictionary(tokens)
corpus = [dictionary.doc2bow(doc) for doc in tokens]
# Make a index to word dictionary.
id2word = dictionary.id2token
lda_model = LdaMulticore(corpus=corpus, id2word=dictionary, iterations=50, num_topics=150, workers = 8, passes=10, alpha='asymmetric')
#lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

In [34]:
# setup: get the model's topics in their native ordering...
all_topics = lda_model.print_topics()
# ...then create a empty list per topic to collect the docs:
docs_per_topic = [[] for _ in all_topics]


In [35]:
# now, for every doc...
for doc_id, doc_bow in enumerate(corpus):
    # ...get its topics...
    doc_topics = lda_model.get_document_topics(doc_bow)
    # ...& for each of its topics...
    for topic_id, score in doc_topics:
        # ...add the doc_id & its score to the topic's doc list
        docs_per_topic[topic_id].append((doc_id, score))

for doc_list in docs_per_topic:
    doc_list.sort(key=lambda id_and_score: id_and_score[1], reverse=True)

IndexError: list index out of range

In [33]:
texts_per_topic = []
exclusion_texts = df[df['exclusion'] == 0]['text'].tolist()
for i in range(len(docs_per_topic)):
    doc_ids = docs_per_topic[i][:1000]
    f = open("topic{}_top1k_text.txt".format(i), "w")
    for (id, score) in doc_ids:
        f.write(exclusion_texts[i] + "\n")
        texts_per_topic.append({'topic': i, 'id': id, 'text': exclusion_texts[i], 'score': score})
    f.close()

In [22]:
df_texts = pd.DataFrame.from_dict(texts_per_topic)

In [28]:
f = open("topics.txt", "w")
for topic in lda_model.print_topics(-1):
    f.write(str(topic) + "\n")
f.close()

# Non Crisis Only - articles WITH exclusion words

In [36]:
tokens = df[df['exclusion'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 77744 documents


[(0,
  '0.018*"border" + 0.011*"migrants" + 0.009*"immigration" + 0.007*"asylum" + 0.006*"mexico" + 0.005*"children" + 0.005*"country" + 0.005*"refugees" + 0.005*"officials" + 0.004*"crisis"'),
 (1,
  '0.007*"world" + 0.007*"europe" + 0.007*"political" + 0.006*"european" + 0.006*"government" + 0.005*"new" + 0.005*"germany" + 0.005*"party" + 0.005*"country" + 0.005*"countries"'),
 (2,
  '0.010*"kosovo" + 0.006*"government" + 0.006*"bosnia" + 0.005*"president" + 0.005*"serbs" + 0.005*"ethnic" + 0.005*"war" + 0.005*"serbian" + 0.005*"cuba" + 0.004*"milosevic"'),
 (3,
  '0.011*"church" + 0.006*"muslim" + 0.006*"religious" + 0.005*"catholic" + 0.004*"muslims" + 0.004*"french" + 0.004*"islamic" + 0.004*"pope" + 0.004*"women" + 0.003*"france"'),
 (4,
  '0.007*"school" + 0.007*"children" + 0.005*"health" + 0.004*"family" + 0.004*"care" + 0.004*"students" + 0.004*"county" + 0.004*"community" + 0.004*"police" + 0.003*"work"'),
 (5,
  '0.004*"new" + 0.003*"life" + 0.003*"world" + 0.003*"way" + 0.

In [54]:
lda_model.

TypeError: get_topic_terms() missing 1 required positional argument: 'topicid'

# Undocumented immigrant/immigrants

In [20]:
tokens = df[df['undocumented'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 1302 documents


[(0,
  '0.012*"immigrants" + 0.011*"mexico" + 0.009*"mexican" + 0.007*"undocumented" + 0.007*"states" + 0.007*"immigration" + 0.006*"new" + 0.006*"united" + 0.006*"illegal" + 0.005*"workers"'),
 (1,
  '0.017*"trump" + 0.012*"house" + 0.011*"democrats" + 0.009*"president" + 0.008*"republicans" + 0.008*"senate" + 0.006*"immigration" + 0.006*"republican" + 0.005*"congress" + 0.005*"gop"'),
 (2,
  '0.040*"trump" + 0.029*"biden" + 0.019*"president" + 0.015*"immigration" + 0.011*"administration" + 0.010*"border" + 0.009*"policy" + 0.008*"states" + 0.007*"new" + 0.007*"united"'),
 (3,
  '0.004*"justice" + 0.003*"polanco" + 0.003*"new" + 0.003*"book" + 0.003*"city" + 0.003*"american" + 0.003*"texas" + 0.003*"world" + 0.003*"california" + 0.003*"state"'),
 (4,
  '0.010*"libre" + 0.007*"company" + 0.006*"immigration" + 0.005*"donovan" + 0.005*"children" + 0.004*"child" + 0.004*"bond" + 0.004*"immigrants" + 0.004*"flores" + 0.004*"dcs"'),
 (5,
  '0.013*"health" + 0.011*"county" + 0.010*"care" + 0

# refugee/refugees

In [21]:
tokens = df[df['refugee'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 25086 documents


[(0,
  '0.009*"government" + 0.007*"refugees" + 0.006*"turkey" + 0.006*"war" + 0.005*"military" + 0.005*"international" + 0.005*"united" + 0.005*"troops" + 0.005*"officials" + 0.005*"aid"'),
 (1,
  '0.007*"food" + 0.005*"refugees" + 0.005*"water" + 0.004*"million" + 0.004*"aid" + 0.004*"children" + 0.004*"city" + 0.004*"government" + 0.004*"new" + 0.003*"world"'),
 (2,
  '0.004*"new" + 0.004*"world" + 0.004*"life" + 0.003*"film" + 0.003*"story" + 0.003*"american" + 0.003*"book" + 0.002*"director" + 0.002*"war" + 0.002*"family"'),
 (3,
  '0.016*"iraq" + 0.012*"iraqi" + 0.007*"kuwait" + 0.007*"hussein" + 0.006*"saddam" + 0.006*"baghdad" + 0.005*"hong" + 0.005*"kong" + 0.005*"iraqis" + 0.004*"war"'),
 (4,
  '0.009*"president" + 0.008*"clinton" + 0.007*"states" + 0.007*"administration" + 0.006*"haiti" + 0.006*"united" + 0.006*"immigration" + 0.006*"policy" + 0.004*"refugees" + 0.004*"american"'),
 (5,
  '0.006*"canada" + 0.005*"refugees" + 0.005*"new" + 0.004*"school" + 0.004*"refugee" + 0

# aslyum seeker / seekers

In [23]:
tokens = df[df['asylum'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 2078 documents


[(0,
  '0.005*"trump" + 0.004*"president" + 0.004*"state" + 0.004*"new" + 0.003*"going" + 0.003*"women" + 0.003*"country" + 0.002*"house" + 0.002*"city" + 0.002*"group"'),
 (1,
  '0.023*"mexico" + 0.015*"border" + 0.012*"trump" + 0.011*"migrants" + 0.010*"mexican" + 0.009*"asylum" + 0.008*"united" + 0.008*"states" + 0.006*"central" + 0.006*"immigration"'),
 (2,
  '0.013*"migrants" + 0.011*"europe" + 0.010*"european" + 0.010*"border" + 0.009*"asylum" + 0.008*"refugees" + 0.007*"countries" + 0.006*"crisis" + 0.006*"seekers" + 0.005*"turkey"'),
 (3,
  '0.018*"refugees" + 0.007*"asylum" + 0.006*"refugee" + 0.005*"country" + 0.005*"seekers" + 0.004*"border" + 0.004*"war" + 0.004*"europe" + 0.004*"family" + 0.003*"north"'),
 (4,
  '0.011*"party" + 0.008*"germany" + 0.008*"merkel" + 0.005*"right" + 0.005*"political" + 0.005*"german" + 0.005*"country" + 0.004*"new" + 0.004*"europe" + 0.004*"government"'),
 (5,
  '0.016*"asylum" + 0.008*"seekers" + 0.006*"migrants" + 0.005*"country" + 0.005*"fa

# migrant / migrants

In [25]:
tokens = df[df['migrant'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 29815 documents


[(0,
  '0.009*"church" + 0.008*"canada" + 0.005*"french" + 0.005*"catholic" + 0.004*"canadian" + 0.004*"new" + 0.004*"toronto" + 0.004*"world" + 0.003*"national" + 0.003*"quebec"'),
 (1,
  '0.011*"police" + 0.007*"directed" + 0.005*"written" + 0.005*"new" + 0.004*"haiti" + 0.004*"officers" + 0.004*"hbox" + 0.003*"miami" + 0.003*"film" + 0.003*"photo"'),
 (2,
  '0.004*"police" + 0.004*"day" + 0.003*"water" + 0.003*"old" + 0.003*"new" + 0.003*"city" + 0.003*"man" + 0.003*"home" + 0.002*"south" + 0.002*"men"'),
 (3,
  '0.008*"china" + 0.006*"mexico" + 0.006*"chinese" + 0.005*"government" + 0.005*"country" + 0.005*"economic" + 0.004*"world" + 0.004*"workers" + 0.004*"new" + 0.003*"american"'),
 (4,
  '0.004*"life" + 0.004*"film" + 0.003*"family" + 0.003*"new" + 0.003*"movie" + 0.003*"story" + 0.003*"director" + 0.003*"minutes" + 0.002*"world" + 0.002*"love"'),
 (5,
  '0.010*"school" + 0.007*"state" + 0.007*"city" + 0.006*"students" + 0.005*"county" + 0.005*"schools" + 0.005*"california" + 

# dreamer / dreamers / daca

In [26]:
tokens = df[df['dreamer'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 998 documents


[(0,
  '0.005*"chicago" + 0.004*"city" + 0.003*"school" + 0.003*"henry" + 0.003*"life" + 0.003*"family" + 0.003*"new" + 0.003*"nov" + 0.003*"university" + 0.002*"good"'),
 (1,
  '0.008*"libre" + 0.005*"company" + 0.005*"american" + 0.005*"immigration" + 0.005*"states" + 0.005*"donovan" + 0.004*"united" + 0.004*"flores" + 0.004*"immigrants" + 0.003*"bond"'),
 (2,
  '0.031*"ins" + 0.004*"free" + 0.003*"steven" + 0.003*"new" + 0.003*"theatre" + 0.003*"work" + 0.003*"friday" + 0.003*"art" + 0.002*"play" + 0.002*"life"'),
 (3,
  '0.024*"biden" + 0.020*"president" + 0.020*"trump" + 0.014*"immigration" + 0.011*"border" + 0.009*"policy" + 0.008*"joe" + 0.007*"new" + 0.007*"elect" + 0.007*"mayorkas"'),
 (4,
  '0.006*"new" + 0.004*"book" + 0.004*"city" + 0.004*"world" + 0.004*"life" + 0.003*"history" + 0.003*"york" + 0.003*"american" + 0.002*"war" + 0.002*"work"'),
 (5,
  '0.010*"stage" + 0.008*"hall" + 0.008*"fiction" + 0.005*"dooley" + 0.005*"mudd" + 0.004*"noon" + 0.004*"times" + 0.004*"prese

# unaccompanied

In [27]:
tokens = df[df['unaccompanied'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 1739 documents


[(0,
  '0.029*"children" + 0.022*"border" + 0.009*"administration" + 0.008*"biden" + 0.007*"patrol" + 0.007*"unaccompanied" + 0.006*"facilities" + 0.006*"crisis" + 0.006*"texas" + 0.005*"officials"'),
 (1,
  '0.039*"border" + 0.017*"children" + 0.009*"migrants" + 0.008*"administration" + 0.008*"patrol" + 0.008*"families" + 0.007*"officials" + 0.007*"unaccompanied" + 0.006*"immigration" + 0.006*"mexico"'),
 (2,
  '0.024*"children" + 0.013*"immigration" + 0.011*"asylum" + 0.007*"border" + 0.006*"parents" + 0.006*"united" + 0.006*"court" + 0.006*"states" + 0.005*"country" + 0.005*"family"'),
 (3,
  '0.013*"migrants" + 0.011*"camp" + 0.006*"europe" + 0.006*"boat" + 0.005*"french" + 0.005*"britain" + 0.005*"france" + 0.004*"authorities" + 0.004*"calais" + 0.004*"migrant"'),
 (4,
  '0.008*"cuba" + 0.007*"cuban" + 0.006*"children" + 0.006*"refugees" + 0.005*"american" + 0.004*"florida" + 0.004*"government" + 0.004*"cubans" + 0.003*"new" + 0.003*"refugee"'),
 (5,
  '0.004*"refugees" + 0.003*"a

# citizenship

In [28]:
tokens = df[df['citizenship'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 3435 documents


[(0,
  '0.005*"new" + 0.004*"country" + 0.004*"government" + 0.004*"party" + 0.003*"president" + 0.003*"minister" + 0.003*"canada" + 0.002*"war" + 0.002*"world" + 0.002*"political"'),
 (1,
  '0.011*"court" + 0.006*"trump" + 0.005*"census" + 0.004*"new" + 0.004*"law" + 0.004*"president" + 0.003*"state" + 0.003*"justice" + 0.003*"department" + 0.003*"case"'),
 (2,
  '0.008*"rohingya" + 0.007*"government" + 0.006*"refugees" + 0.006*"country" + 0.005*"myanmar" + 0.004*"canada" + 0.004*"rights" + 0.004*"refugee" + 0.004*"state" + 0.004*"citizenship"'),
 (3,
  '0.005*"american" + 0.005*"ins" + 0.005*"border" + 0.005*"new" + 0.005*"mexico" + 0.004*"america" + 0.004*"immigration" + 0.004*"children" + 0.004*"asylum" + 0.004*"country"'),
 (4,
  '0.004*"president" + 0.003*"city" + 0.003*"trump" + 0.003*"care" + 0.003*"health" + 0.003*"american" + 0.003*"going" + 0.003*"new" + 0.003*"country" + 0.003*"day"'),
 (5,
  '0.006*"school" + 0.004*"students" + 0.004*"education" + 0.004*"new" + 0.004*"chil

# Immigration Reform

In [29]:
tokens = df[df['immigration_reform'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 2112 documents


[(0,
  '0.004*"new" + 0.003*"house" + 0.003*"american" + 0.003*"president" + 0.003*"government" + 0.003*"state" + 0.003*"district" + 0.003*"cupich" + 0.003*"act" + 0.002*"immigration"'),
 (1,
  '0.005*"district" + 0.004*"immigration" + 0.004*"county" + 0.004*"city" + 0.004*"latino" + 0.003*"country" + 0.003*"american" + 0.003*"latinos" + 0.003*"state" + 0.003*"new"'),
 (2,
  '0.005*"new" + 0.004*"business" + 0.004*"company" + 0.004*"immigration" + 0.003*"growth" + 0.003*"world" + 0.003*"million" + 0.003*"workers" + 0.003*"population" + 0.003*"government"'),
 (3,
  '0.009*"workers" + 0.008*"immigration" + 0.007*"undocumented" + 0.006*"immigrants" + 0.005*"work" + 0.005*"family" + 0.004*"legal" + 0.004*"state" + 0.004*"status" + 0.003*"labor"'),
 (4,
  '0.008*"applause" + 0.007*"going" + 0.007*"president" + 0.005*"senator" + 0.005*"country" + 0.005*"need" + 0.005*"right" + 0.005*"health" + 0.005*"want" + 0.004*"care"'),
 (5,
  '0.016*"immigration" + 0.008*"reform" + 0.008*"arizona" + 0.0

In [31]:
# border / borders

In [32]:
tokens = df[df['border'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 56637 documents


[(0,
  '0.006*"water" + 0.006*"children" + 0.006*"border" + 0.004*"food" + 0.004*"family" + 0.004*"home" + 0.004*"city" + 0.003*"day" + 0.003*"old" + 0.003*"mexico"'),
 (1,
  '0.004*"new" + 0.003*"life" + 0.002*"book" + 0.002*"world" + 0.002*"story" + 0.002*"family" + 0.002*"american" + 0.002*"man" + 0.002*"old" + 0.002*"film"'),
 (2,
  '0.006*"market" + 0.005*"new" + 0.005*"bank" + 0.005*"billion" + 0.005*"mexico" + 0.005*"financial" + 0.005*"economic" + 0.004*"economy" + 0.004*"companies" + 0.004*"company"'),
 (3,
  '0.013*"trump" + 0.012*"border" + 0.010*"president" + 0.007*"immigration" + 0.007*"house" + 0.006*"administration" + 0.005*"biden" + 0.004*"mexico" + 0.004*"security" + 0.004*"new"'),
 (4,
  '0.010*"state" + 0.008*"city" + 0.007*"county" + 0.006*"california" + 0.005*"new" + 0.004*"school" + 0.004*"public" + 0.004*"tax" + 0.004*"million" + 0.003*"district"'),
 (5,
  '0.020*"russia" + 0.016*"russian" + 0.012*"ukraine" + 0.010*"soviet" + 0.008*"moscow" + 0.008*"nato" + 0.007

# Detention

In [33]:
tokens = df[df['detention'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 3387 documents


[(0,
  '0.008*"bosnia" + 0.006*"serb" + 0.006*"bosnian" + 0.006*"war" + 0.005*"serbs" + 0.004*"serbian" + 0.004*"ethnic" + 0.004*"camps" + 0.003*"international" + 0.003*"officials"'),
 (1,
  '0.012*"migrants" + 0.011*"asylum" + 0.008*"mexico" + 0.008*"refugees" + 0.006*"united" + 0.005*"border" + 0.005*"country" + 0.005*"states" + 0.004*"refugee" + 0.004*"human"'),
 (2,
  '0.005*"trump" + 0.004*"state" + 0.003*"going" + 0.003*"know" + 0.003*"president" + 0.003*"syria" + 0.003*"think" + 0.003*"new" + 0.002*"house" + 0.002*"right"'),
 (3,
  '0.008*"prison" + 0.007*"director" + 0.007*"inmates" + 0.005*"min" + 0.005*"federal" + 0.005*"cuban" + 0.005*"hostages" + 0.004*"atlanta" + 0.004*"cubans" + 0.004*"grade"'),
 (4,
  '0.016*"president" + 0.015*"trump" + 0.014*"biden" + 0.008*"immigration" + 0.007*"obama" + 0.006*"border" + 0.006*"policy" + 0.006*"new" + 0.005*"states" + 0.005*"country"'),
 (5,
  '0.005*"county" + 0.005*"school" + 0.005*"health" + 0.003*"state" + 0.003*"staff" + 0.003*"c

# Deport / deportation

In [34]:
tokens = df[df['deport'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 5045 documents


[(0,
  '0.005*"school" + 0.004*"students" + 0.003*"government" + 0.003*"new" + 0.003*"immigration" + 0.003*"family" + 0.003*"children" + 0.002*"country" + 0.002*"home" + 0.002*"united"'),
 (1,
  '0.006*"refugees" + 0.006*"kosovo" + 0.005*"war" + 0.005*"nato" + 0.005*"government" + 0.004*"europe" + 0.004*"canada" + 0.003*"world" + 0.003*"minister" + 0.003*"ethnic"'),
 (2,
  '0.011*"immigration" + 0.007*"refugees" + 0.007*"immigrants" + 0.006*"asylum" + 0.006*"law" + 0.005*"illegal" + 0.005*"refugee" + 0.005*"government" + 0.005*"new" + 0.004*"country"'),
 (3,
  '0.007*"trump" + 0.006*"president" + 0.005*"government" + 0.005*"china" + 0.005*"officials" + 0.004*"venezuela" + 0.004*"border" + 0.004*"venezuelans" + 0.003*"week" + 0.003*"north"'),
 (4,
  '0.007*"maupin" + 0.005*"scottsdale" + 0.005*"march" + 0.004*"minutes" + 0.004*"contains" + 0.004*"movie" + 0.004*"free" + 0.003*"com" + 0.003*"film" + 0.003*"new"'),
 (5,
  '0.004*"city" + 0.003*"film" + 0.003*"new" + 0.003*"federal" + 0.00

# Sanctuary

In [35]:
tokens = df[df['sanctuary'] == 1]['tokens'].tolist()
lda_model = runLDA(tokens)
print("Includes {} documents".format(len(tokens)))
lda_model.print_topics(-1)

Includes 1666 documents


[(0,
  '0.011*"refugees" + 0.005*"border" + 0.005*"war" + 0.005*"europe" + 0.005*"government" + 0.004*"refugee" + 0.004*"migrants" + 0.004*"turkey" + 0.004*"officials" + 0.004*"president"'),
 (1,
  '0.006*"abrams" + 0.006*"open" + 0.005*"garden" + 0.004*"subc" + 0.004*"palace" + 0.003*"album" + 0.003*"mcsally" + 0.003*"leon" + 0.003*"state" + 0.003*"education"'),
 (2,
  '0.006*"directed" + 0.003*"written" + 0.003*"new" + 0.003*"dooley" + 0.002*"family" + 0.002*"government" + 0.002*"life" + 0.002*"oil" + 0.002*"hodel" + 0.002*"old"'),
 (3,
  '0.004*"government" + 0.003*"new" + 0.003*"american" + 0.002*"refugees" + 0.002*"day" + 0.002*"contras" + 0.002*"sudan" + 0.002*"country" + 0.002*"children" + 0.002*"million"'),
 (4,
  '0.008*"military" + 0.008*"iraq" + 0.007*"pakistan" + 0.007*"government" + 0.007*"war" + 0.005*"forces" + 0.005*"president" + 0.004*"afghanistan" + 0.004*"iraqi" + 0.004*"officials"'),
 (5,
  '0.008*"county" + 0.008*"city" + 0.005*"park" + 0.005*"chris" + 0.004*"new" 

# 

In [ ]:
tokens = []

# Tags I want to remove from the text
#removal= ['ADV','PRON','CCONJ','PUNCT','PART','DET','ADP','SPACE', 'NUM', 'SYM']
removal= ['PUNCT','SPACE']

for summary in nlp.pipe(fulltext):
   proj_tok = [token.lemma_.lower() for token in summary if token.pos_ not in removal and not token.is_stop and token.is_alpha and not 'say' and not 'year']
   tokens.append(proj_tok)

In [30]:
lda_display = pyLDAvis.gensim_models.prepare(lda_model, corpus, dictionary)
pyLDAvis.display(lda_display)

/opt/homebrew/lib/python3.9/site-packages/pyLDAvis/_prepare.py:246: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only
  default_term_info = default_term_info.sort_values(
/opt/homebrew/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/opt/homebrew/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/opt/homebrew/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the imp module is deprecated in favour of importlib; see the module's documentation for alternative uses
  from imp import reload
/opt/homebrew/lib/python3.9/site-packages/past/builtins/misc.py:45: DeprecationWarning: the im